# Assignment 2

Haoyuan Wang

Andy Thai

In [1]:
# Import statements
import csv
from pprint import pprint
from collections import defaultdict
import pandas as pd 
import numpy as np
from sklearn import linear_model
from sklearn import svm

In [2]:
# Read in input csvs
df = pd.read_table("anime.csv", sep=",")
us = pd.read_table("rating.csv", sep=",")

In [3]:
# Initialize variables
animeList = {}                    # Anime and their data
genreList = defaultdict(list)     # Animes sorted by genre
userList = defaultdict(list)      # User's list of anime and rating in a (anime_id,rating) structure
userRating = defaultdict(list)    # User's rating
userCategory = defaultdict(set)   # User's list of categories they have watched

## Set up dictionary data structures

In [4]:
# To get data from animeList. dictionary = animeList['id']['data']
def getData(dictionary):
    if not dictionary.isnull().values[0]:
        return dictionary.values[0]
    else:
        return 0

In [5]:
# Get category data from getData
def getCategory(data):
    cat=[]
    if data:
        for x in data.split(', '):
            cat.append(x)
    return cat

In [6]:
# Compile the animeList and genreList
for index, row in df.iterrows():
    animeList[row['anime_id']]=df.loc[[index]]
    if not df.loc[[index]]['genre'].isnull().values[0]:
        for x in row['genre'].split(', '):
            genreList[x].append(row['anime_id'])

In [7]:
# Compile the userList and userRating list
for index, row in us.iterrows():
    userList[row['user_id']].append(row['anime_id'])
    if row['rating'] != -1:
        userRating[row['user_id']].append(row['rating'])

In [8]:
# Compile the user category list (do not need to run this, very long)
for index, row in us.iterrows():
    if int(row['anime_id']) in animeList:
        catList= getCategory(getData(animeList[int(row['anime_id'])]['genre']))
        for x in catList:
            userCategory[row['user_id']].add(x)

In [8]:
# Average rating per user including -1 for no review
averageUser = defaultdict(float)
stdUser = defaultdict(float)
for key in userRating:
    averageUser[key] = np.mean(userRating[key])
    stdUser[key] = np.std(userRating[key])

## Basic Statistics about Dataset

In [9]:
# Get mean and standard deviation 
mean_ratings = {}
std_ratings = {}

genres = genreList.keys()
for genre in genres:
    animeIDs = genreList[genre]
    avg_list = []
    for anime in animeIDs:
        avg_list.append(int(getData(animeList[anime]['rating'])))
    mean_ratings[genre] = np.mean(avg_list)
    std_ratings[genre] = np.std(avg_list)

In [11]:
# Mean
pprint(mean_ratings)

{'Action': 6.1363796133567661,
 'Adventure': 6.1771720613287906,
 'Cars': 5.958333333333333,
 'Comedy': 6.0508073196986008,
 'Dementia': 4.5041666666666664,
 'Demons': 6.0374149659863949,
 'Drama': 6.3908730158730158,
 'Ecchi': 6.0910518053375196,
 'Fantasy': 6.0134257254222607,
 'Game': 6.2320441988950277,
 'Harem': 6.381703470031546,
 'Hentai': 5.6371603856266432,
 'Historical': 6.2270471464019854,
 'Horror': 5.8644986449864502,
 'Josei': 6.666666666666667,
 'Kids': 5.6314481044126783,
 'Magic': 6.0552699228791775,
 'Martial Arts': 6.3094339622641513,
 'Mecha': 6.0688559322033901,
 'Military': 6.352112676056338,
 'Music': 5.3360465116279068,
 'Mystery': 6.6141414141414145,
 'Parody': 5.9779411764705879,
 'Police': 6.563451776649746,
 'Psychological': 6.462882096069869,
 'Romance': 6.3879781420765029,
 'Samurai': 6.3040540540540544,
 'School': 6.2459016393442619,
 'Sci-Fi': 6.1251207729468602,
 'Seinen': 6.3016453382084094,
 'Shoujo': 6.2951907131011611,
 'Shoujo Ai': 6.36363636363636

In [ ]:
# Standard deviation 
pprint(std_ratings)

## Baseline Code

## Create Feature Vectors (Genre One-hot Encoding)

In [ ]:
# Compile the feature vector by using one-hot encoding for genres
genreOrder = sorted(genreList.keys())
feat = []
for index, row in us.iterrows():
    temp = []
    if int(row['anime_id']) in animeList:
        catList = getCategory(getData(animeList[int(row['anime_id'])]['genre']))
    for x in genreOrder:
        if x in catList:
            temp.append(1)
        else:
            temp.append(0)
    feat.append(temp)

In [ ]:
# Create X feature and Y feature
# X = one hot encoding genres
# Y = Rating by user for each anime (including -1)
X_featureSet = feat
Y_featureSet = [row['rating'] for index,row in us.iterrows()]

In [ ]:
len(X_featureSet) / 3

In [ ]:
# I gave up running this. It never finished.... I am not sure whether prediction rating by genre is a good idea. 
# Test on validation set
lam = [0.01, 0.1, 1, 10]

# Calculate accuracy
def difference(pred,act):
    correct = 0
    
    for i in range(0, len(pred)):
        if pred[i] == act[i]:
            correct = correct + 1
    return float(correct) / len(pred)
    
# Run linear SVM
clf = svm.LinearSVC(C=1)
clf.fit(X_featureSet[:int(len(X_featureSet) / 10)], Y_featureSet[:int(len(Y_featureSet) / 10)])

valid_predictions = clf.predict(X_featureSet[int(len(X_featureSet) / 3):int(2 * len(X_featureSet) / 3)])
print("lambda = " + str(l) + ":\taccuracy_valid=" + str(difference(valid_predictions, Y_featureSet[int(len(Y_featureSet) / 3):int(2 * len(Y_featureSet) / 3)])))

## Cosine Similarity Calculations

In [12]:
from scipy.spatial.distance import cosine

In [13]:
# Cosine similarity between animes
genereList = sorted(genreList.keys())

animeFeatureList = []
for key in animeList:
    temp = []
    catList = getCategory(getData(animeList[key]['genre']))
    for x in genreList:
        if x in catList:
            temp.append(1)
        else:
            temp.append(0)
    animeFeatureList.append((key,temp))

In [108]:
# Get cosine similarities for each anime ID with others
# This takes a while too, but it seems to work as intended i think.
cosine_anime = defaultdict(float)
temp = defaultdict(list)

for i in range(0,len(animeFeatureList)):
    # id1 = [] # (id2, cos_sim)
    
    for j in range(i,len(animeFeatureList)):
        id2 = animeFeatureList[j][0]
        if id2 != animeFeatureList[i][0]:
            cos_sim = 1 - cosine(animeFeatureList[i][1], animeFeatureList[j][1])
            temp[i].append((id2, cos_sim))
            temp[id2].append((i, cos_sim))
    
    cosine_anime[animeFeatureList[i][0]] = sorted(temp[i], key=lambda x:x[1], reverse=True)[:10]
    del temp[i]

C:\Users\Andy\Anaconda3\lib\site-packages\scipy\spatial\distance.py:505: RuntimeWarning: invalid value encountered in true_divide
  dist = 1.0 - np.dot(u, v) / (norm(u) * norm(v))


In [110]:
for key in cosine_anime:
    if len(cosine_anime[key])<10:
        pprint((key,cosine_anime[key]))

(26031,
 [(10368, 1.0),
  (9352, 1.0),
  (5541, 1.0),
  (9316, 1.0),
  (5543, 1.0),
  (5621, 1.0),
  (6133, 1.0),
  (26081, 1.0),
  (34399, 0.57735026918962584)])
(34399,
 [(10368, 0.57735026918962584),
  (9352, 0.57735026918962584),
  (5541, 0.57735026918962584),
  (9316, 0.57735026918962584),
  (5543, 0.57735026918962584),
  (5621, 0.57735026918962584),
  (6133, 0.57735026918962584),
  (26081, 0.57735026918962584)])
(10368,
 [(9352, 1.0),
  (5541, 1.0),
  (9316, 1.0),
  (5543, 1.0),
  (5621, 1.0),
  (6133, 1.0),
  (26081, 1.0)])
(9352,
 [(5541, 1.0),
  (9316, 1.0),
  (5543, 1.0),
  (5621, 1.0),
  (6133, 1.0),
  (26081, 1.0)])
(5541, [(9316, 1.0), (5543, 1.0), (5621, 1.0), (6133, 1.0), (26081, 1.0)])
(9316, [(5543, 1.0), (5621, 1.0), (6133, 1.0), (26081, 1.0)])
(5543, [(5621, 1.0), (6133, 1.0), (26081, 1.0)])
(6133, [(26081, 1.0)])


In [93]:
pprint(animeList[26081])

       anime_id                              name   genre   type episodes  \
12293     26081  Yasuji no Pornorama: Yacchimae!!  Hentai  Movie        1   

       rating  members  
12293    5.46      142  


In [109]:
# Write to file
with open('E:/anime_cosine_sim.csv', 'w') as csv_file:
    writer = csv.writer(csv_file)
    writer.writerow(['anime_id','top 10 cosine similarities'])
    for key, value in cosine_anime.items():
        writer.writerow([key, value])

In [32]:
# Read in saved anime cosine csv
cos_sim_csv = pd.read_table("E:/anime_cosine_sim.csv", sep=",")

In [85]:
def getCosineSim(dataList):
    cosineList=[]
    dataList=dataList.replace(" ","")
    dataList=dataList.replace("(","")
    if '),' in dataList:
        parsed_data=dataList[1:len(dataList)-1].split("),")
        format_data=map((lambda x :x.split(',')),parsed_data)
        data=list(format_data)
        data[len(data)-1][1]=data[len(data)-1][1].replace(")","")
    else:
        dataList=dataList.replace(")","")
        dataList=dataList.replace("[","")
        dataList=dataList.replace("]","")
        data=[dataList.split(",")]
    return data

In [89]:
cosine_sim_table=defaultdict(list)
for key, row in cos_sim_csv.iterrows():
    pprint(row)
    data_list=getCosineSim(row['top 10 cosine similarities'])
    for data in data_list:
        cosine_sim_table[row['anime_id']].append((int(data[0]),float(data[1])))
    

anime_id                                                                  32281
top 10 cosine similarities    [(547, 1.0), (546, 1.0), (14669, 0.89442719099...
Name: 0, dtype: object
'[547,1.0),546,1.0),14669,0.89442719099991586),28725,0.86602540378443871),6351,0.86602540378443871),10067,0.86602540378443871),2129,0.86602540378443871),8481,0.86602540378443871),20903,0.86602540378443871),2927,0.86602540378443871)]'
anime_id                                                                   5114
top 10 cosine similarities    [(121, 0.93541434669348522), (9135, 0.93541434...
Name: 1, dtype: object
'[121,0.93541434669348522),9135,0.93541434669348522),6421,0.92582009977255142),18115,0.84515425472851646),14513,0.84515425472851646),31741,0.84515425472851646),22097,0.84515425472851646),8086,0.84515425472851646),6046,0.84515425472851646),807,0.84515425472851646)]'
anime_id                                                                  28977
top 10 cosine similarities    [(9969, 0.99999999999999

'[2174,0.89442719099991586),5854,0.79999999999999982),4663,0.79999999999999982),30965,0.79999999999999982),1773,0.7745966692414834),5226,0.7745966692414834),2543,0.7745966692414834),4094,0.7745966692414834),28041,0.7745966692414834),45,0.73029674334022143)]'
anime_id                                                                  11979
top 10 cosine similarities    [(11977, 1.0), (4715, 0.75), (23283, 0.7071067...
Name: 107, dtype: object
'[11977,1.0),4715,0.75),23283,0.70710678118654746),7420,0.70710678118654746),9940,0.70710678118654746),28223,0.67082039324993692),14353,0.67082039324993692),7193,0.67082039324993692),3420,0.67082039324993692),323,0.61237243569579458)]'
anime_id                                                                   7655
top 10 cosine similarities    [(9890, 1.0000000000000002), (6076, 1.00000000...
Name: 108, dtype: object
'[9890,1.0000000000000002),6076,1.0000000000000002),627,0.86602540378443871),558,0.86602540378443871),3226,0.86602540378443871),24277,0

Name: 491, dtype: object
'[246,0.79999999999999982),626,0.79999999999999982),660,0.79999999999999982),445,0.79999999999999982),4886,0.79056941504209477),908,0.7745966692414834),2385,0.7745966692414834),20871,0.7745966692414834),590,0.7745966692414834),249,0.7453559924999299)]'
anime_id                                                                  27989
top 10 cosine similarities    [(31665, 1.0000000000000002), (19177, 1.000000...
Name: 492, dtype: object
'[31665,1.0000000000000002),19177,1.0000000000000002),23043,0.86602540378443871),17020,0.86602540378443871),10935,0.81649658092772592),31989,0.81649658092772592),6361,0.81649658092772592),21189,0.81649658092772592),30419,0.81649658092772592),26453,0.81649658092772592)]'
anime_id                                                                   5630
top 10 cosine similarities    [(6637, 0.92582009977255142), (13863, 0.845154...
Name: 493, dtype: object
'[6637,0.92582009977255142),13863,0.84515425472851646),1921,0.77151674981045948),

'[852,0.81649658092772615),694,0.81649658092772615),119,0.81649658092772615),470,0.81649658092772615),11433,0.73029674334022143),18671,0.73029674334022143),27601,0.73029674334022143),31680,0.73029674334022143),19021,0.73029674334022143),23447,0.73029674334022143)]'
anime_id                                                                     17
top 10 cosine similarities    [(30652, 1.0), (34367, 1.0), (814, 0.866025403...
Name: 976, dtype: object
'[30652,1.0),34367,1.0),814,0.86602540378443871),10378,0.86602540378443871),8557,0.86602540378443871),13267,0.86602540378443871),32648,0.86602540378443871),3568,0.86602540378443871),32871,0.86602540378443871),26395,0.86602540378443871)]'
anime_id                                                                   3931
top 10 cosine similarities    [(12725, 0.99999999999999978), (821, 0.9999999...
Name: 977, dtype: object
'[12725,0.99999999999999978),821,0.99999999999999978),5228,0.99999999999999978),822,0.99999999999999978),2608,0.89442719099991

'[20423,0.99999999999999978),2369,0.81649658092772592),7112,0.81649658092772592),8162,0.81649658092772592),24459,0.70710678118654746),2672,0.70710678118654746),30187,0.70710678118654746),2675,0.70710678118654746),2660,0.70710678118654746),2667,0.70710678118654746)]'
anime_id                                                                    435
top 10 cosine similarities    [(10028, 0.99999999999999978), (13931, 0.93541...
Name: 1470, dtype: object
'[10028,0.99999999999999978),13931,0.93541434669348522),1578,0.87499999999999978),103,0.86602540378443871),3298,0.86602540378443871),142,0.8249579113843053),1744,0.8249579113843053),100,0.80178372573727308),393,0.80178372573727308),2535,0.80178372573727308)]'
anime_id                                                                  10110
top 10 cosine similarities    [(25099, 0.99999999999999978), (14199, 0.99999...
Name: 1471, dtype: object
'[25099,0.99999999999999978),14199,0.99999999999999978),10611,0.99999999999999978),31797,0.9999999999

...

Name: 10508, dtype: object
'[16746,0.57735026918962584),19555,0.57735026918962584),11681,0.5),15399,0.5),32732,0.35355339059327373),23723,0.35355339059327373),23915,0.35355339059327373),7459,0.35355339059327373),29369,0.35355339059327373),12529,0.35355339059327373)]'
anime_id                                                                  29457
top 10 cosine similarities    [(29856, 0.99999999999999978), (32799, 0.99999...
Name: 10509, dtype: object
'[29856,0.99999999999999978),32799,0.99999999999999978),31872,0.99999999999999978),30582,0.81649658092772592),25149,0.70710678118654746),28591,0.70710678118654746),33887,0.70710678118654746),24803,0.70710678118654746),32388,0.70710678118654746),29800,0.70710678118654746)]'
anime_id                                                                  25987
top 10 cosine similarities    [(8189, 0.99999999999999978), (33533, 0.816496...
Name: 10510, dtype: object
'[8189,0.99999999999999978),33533,0.81649658092772592),4775,0.81649658092772592),716

anime_id                                                                  34100
top 10 cosine similarities    [(33049, 0.75), (33050, 0.75), (34338, nan), (...
Name: 10979, dtype: object
'[33049,0.75),33050,0.75),34338,nan),34332,nan),221,0.5),34280,0.28867513459481287),34488,0.28867513459481287),33731,0.25),33457,0.25),34427,0.0)]'
anime_id                                                                  33049
top 10 cosine similarities    [(33050, 1.0), (34338, nan), (34332, nan), (13...
Name: 10980, dtype: object
'[33050,1.0),34338,nan),34332,nan),1331,0.7559289460184544),4127,0.75),33731,0.25),34427,0.0),33203,0.0),33457,0.0),34280,0.0)]'
anime_id                                                                  33050
top 10 cosine similarities    [(34338, nan), (34332, nan), (34485, nan), (33...
Name: 10981, dtype: object
'[34338,nan),34332,nan),34485,nan),33389,nan),1331,0.7559289460184544),4127,0.75),34279,0.70710678118654746),3534,0.67082039324993692),3992,0.61237243569579458),3

'[5455,1.0),10421,1.0),24317,1.0),10851,1.0),2590,1.0),9588,1.0),4714,1.0),13325,1.0),2533,1.0),29915,1.0)]'
anime_id                                                                   5455
top 10 cosine similarities    [(10421, 1.0), (24317, 1.0), (10851, 1.0), (25...
Name: 11501, dtype: object
'[10421,1.0),24317,1.0),10851,1.0),2590,1.0),9588,1.0),4714,1.0),13325,1.0),2533,1.0),29915,1.0),32267,1.0)]'
anime_id                                                                  10421
top 10 cosine similarities    [(24317, 1.0), (10851, 1.0), (2590, 1.0), (958...
Name: 11502, dtype: object
'[24317,1.0),10851,1.0),2590,1.0),9588,1.0),4714,1.0),13325,1.0),2533,1.0),29915,1.0),32267,1.0),2445,1.0)]'
anime_id                                                                   4057
top 10 cosine similarities    [(2345, 0.86602540378443871), (2479, 0.8660254...
Name: 11503, dtype: object
'[2345,0.86602540378443871),2479,0.86602540378443871),2977,0.86602540378443871),3553,0.86602540378443871),2480,

anime_id                                                          5543
top 10 cosine similarities    [(5621, 1.0), (6133, 1.0), (26081, 1.0)]
Name: 12290, dtype: object
'[5621,1.0),6133,1.0),26081,1.0)]'
anime_id                                             5621
top 10 cosine similarities    [(6133, 1.0), (26081, 1.0)]
Name: 12291, dtype: object
'[6133,1.0),26081,1.0)]'
anime_id                                6133
top 10 cosine similarities    [(26081, 1.0)]
Name: 12292, dtype: object
'[26081,1.0)]'
anime_id                      26081
top 10 cosine similarities       []
Name: 12293, dtype: object
'[]'


ValueError: invalid literal for int() with base 10: ''

In [70]:
len(cosine_sim_table)

12293

**Relevant research article:**

http://jill-jenn.net/_static/works/mangaki-recsys2015.pdf 